In [1]:
import pandas as pd
import numpy as np
import chardet
df_movies=pd.read_csv("/home/pratiksha/Downloads/movies.csv")
df_movies.head()


movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [2]:
df_ratings=pd.read_csv("/home/pratiksha/Downloads/ratings.csv")
df_ratings.head()


userId  movieId  rating
0       1        2     3.5
1       1       29     3.5
2       1       32     3.5
3       1       47     3.5
4       1       50     3.5

In [3]:
movies={}
def add_movie(row):
     movies[row[0]]=row[1]
df_movies.apply(add_movie, axis=1)
movies

{1: 'Toy Story (1995)',
 2: 'Jumanji (1995)',
 3: 'Grumpier Old Men (1995)',
 4: 'Waiting to Exhale (1995)',
 5: 'Father of the Bride Part II (1995)',
 6: 'Heat (1995)',
 7: 'Sabrina (1995)',
 8: 'Tom and Huck (1995)',
 9: 'Sudden Death (1995)',
 10: 'GoldenEye (1995)',
 11: 'American President, The (1995)',
 12: 'Dracula: Dead and Loving It (1995)',
 13: 'Balto (1995)',
 14: 'Nixon (1995)',
 15: 'Cutthroat Island (1995)',
 16: 'Casino (1995)',
 17: 'Sense and Sensibility (1995)',
 18: 'Four Rooms (1995)',
 19: 'Ace Ventura: When Nature Calls (1995)',
 20: 'Money Train (1995)',
 21: 'Get Shorty (1995)',
 22: 'Copycat (1995)',
 23: 'Assassins (1995)',
 24: 'Powder (1995)',
 25: 'Leaving Las Vegas (1995)',
 26: 'Othello (1995)',
 27: 'Now and Then (1995)',
 28: 'Persuasion (1995)',
 29: 'City of Lost Children, The (Cité des enfants perdus, La) (1995)',
 30: 'Shanghai Triad (Yao a yao yao dao waipo qiao) (1995)',
 31: 'Dangerous Minds (1995)',
 32: 'Twelve Monkeys (a.k.a. 12 Monkeys) (199

In [4]:
df=df_ratings
df['title']= df['movieId'].map(lambda x: movies[x])
df.head()

userId  movieId  rating                                              title
0       1        2     3.5                                     Jumanji (1995)
1       1       29     3.5  City of Lost Children, The (Cité des enfants p...
2       1       32     3.5          Twelve Monkeys (a.k.a. 12 Monkeys) (1995)
3       1       47     3.5                        Seven (a.k.a. Se7en) (1995)
4       1       50     3.5                         Usual Suspects, The (1995)

In [5]:
prefs ={}

def add_pref(row):
    if not row[0] in prefs:
        prefs[row[0]] = {}
    prefs[row[0]][movies[row[1]]] = row[2]
df.apply(add_pref, axis=1)
prefs

{1: {'Jumanji (1995)': 3.5,
  'City of Lost Children, The (Cité des enfants perdus, La) (1995)': 3.5,
  'Twelve Monkeys (a.k.a. 12 Monkeys) (1995)': 3.5,
  'Seven (a.k.a. Se7en) (1995)': 3.5,
  'Usual Suspects, The (1995)': 3.5,
  'Rumble in the Bronx (Hont faan kui) (1995)': 3.5,
  'Rob Roy (1995)': 4.0,
  'Clerks (1994)': 4.0,
  'Interview with the Vampire: The Vampire Chronicles (1994)': 4.0,
  'Star Wars: Episode IV - A New Hope (1977)': 4.0,
  'Léon: The Professional (a.k.a. The Professional) (Léon) (1994)': 4.0,
  'Pulp Fiction (1994)': 4.0,
  'Shawshank Redemption, The (1994)': 4.0,
  "What's Eating Gilbert Grape (1993)": 3.5,
  'Mask, The (1994)': 3.5,
  'Blade Runner (1982)': 4.0,
  'Terminator 2: Judgment Day (1991)': 3.5,
  'Silence of the Lambs, The (1991)': 3.5,
  'Dragonheart (1996)': 3.0,
  'Wizard of Oz, The (1939)': 3.5,
  '2001: A Space Odyssey (1968)': 3.5,
  'Escape to Witch Mountain (1975)': 3.5,
  'Die Hard (1988)': 4.0,
  'Fish Called Wanda, A (1988)': 4.0,
  "Mo

In [6]:
from math import sqrt

# returns distance based similarity score for person1 and person2

def sim_distance(prefs, person1, person2):
    sum_of_squares = 0
    common_count = 0
    for movie in prefs[person1]:
        if movie in prefs[person2]:
            sum_of_squares = sum_of_squares + pow(prefs[person1][movie] - prefs[person2][movie], 2)
            common_count = common_count + 1

    if common_count == 0:
        return 0
    else:
        return 1/(1+sum_of_squares)

In [7]:
def sim_jaccard(prefs, p1, p2):
    numerator = 0
    difference = 0
    for movie in prefs[p1]:
        if movie in prefs[p2]:
            numerator = numerator + 1
        else:
            difference = difference + 1
    denominator = len(prefs[p1].keys()) + difference
    return numerator/denominator


In [8]:
def sim_pearson(prefs, p1, p2):
    sum1 = sum(prefs[p1].values())
    sum2 = sum(prefs[p2].values())
    # Get the list of mutually rated items
    si={}
    for item in prefs[p1]:
        if item in prefs[p2]: si[item]=1
    # Find the number of elements
    n=len(si)
    # if they are no ratings in common, return 0
    if n==0: return 0
    # Add up all the preferences
    sum1=sum([prefs[p1][it] for it in si])
    sum2=sum([prefs[p2][it] for it in si])
    # Sum up the squares
    sum1Sq=sum([pow(prefs[p1][it],2) for it in si])
    sum2Sq=sum([pow(prefs[p2][it],2) for it in si])
    # Sum up the products
    pSum=sum([prefs[p1][it]*prefs[p2][it] for it in si])
    # Calculate Pearson score
    num=pSum-(sum1*sum2/n)
    den=sqrt((sum1Sq-pow(sum1,2)/n)*(sum2Sq-pow(sum2,2)/n))
    if den==0: return 0
    r=num/den
    return r


In [9]:
# Returns the best matches for person from the prefs dictionary.
# Number of results and similarity function are optional params.

def topMatches(prefs, person, n=5, similarity=sim_pearson):
     scores = [(similarity(prefs, person, other), other) for other in prefs]

     scores.sort(reverse=True)
     return scores[:n]

In [10]:
# Gets recommendations for a person by using a weighted average
# of every other user's rankings
def getRecommendations(prefs,person,similarity=sim_pearson):
    totals={}
    simSums={}
    for other in prefs:
        # don't compare me to myself
        if other==person: continue
        sim=similarity(prefs,person,other)
        # ignore scores of zero or lower
        if sim<=0: continue
        for item in prefs[other]:
            # only score movies I haven't seen yet
            if item not in prefs[person] or prefs[person][item]==0:
                # Similarity * Score
                totals.setdefault(item,0)
                totals[item]+=prefs[other][item]*sim
                # Sum of similarities
                simSums.setdefault(item,0)
                simSums[item]+=sim
    # Create the normalized list
    rankings=[(total/simSums[item],item) for item,total in totals.items( )]
    # Return the sorted list
    rankings.sort( )
    rankings.reverse( )
    return rankings

In [11]:
def loadMovieLens(path='../Data/movielens'):
    # Get movie titles
    movies={}
    for line in open(path+'/movies.csv'):
        (id,title)=line.split('|')[0:2]
        movies[id]=title
    # Load data
    prefs={}
    for line in open(path+'/ratings.csv'):
        (user,movieid,rating,ts)=line.split('\t')
        prefs.setdefault(user,{})
        prefs[user][movies[movieid]]=float(rating)
    return prefs


In [15]:
pearsonrank=[]
pearsonrank=getRecommendations(prefs,105,similarity=sim_pearson)
pearsonrank

for i in range(0,10):
    print(pearsonrank[i])


(5.000000000000001, 'Tex (1982)')
(5.000000000000001, 'Some Kind of Wonderful (1987)')
(5.000000000000001, 'Shoah (1985)')
(5.000000000000001, 'Running on Empty (1988)')
(5.000000000000001, 'Rumble Fish (1983)')
(5.000000000000001, "Razor's Edge, The (1984)")
(5.000000000000001, 'One Crazy Summer (1986)')
(5.000000000000001, 'Hamburger Hill (1987)')
(5.000000000000001, 'Ballad of Narayama, The (Narayama Bushiko) (1958)')
(5.000000000000001, '1969 (1988)')


In [16]:
jaccardrank=[]
jaccardrank=getRecommendations(prefs,105,similarity=sim_jaccard)
jaccardrank

for i in range(0,10):
    print(jaccardrank[i])

(5.000000000000001, 'Dolls (2002)')
(5.000000000000001, 'CJ7 (Cheung Gong 7 hou) (2008)')
(5.0, 'Youngblood (1986)')
(5.0, 'Yentl (1983)')
(5.0, 'World of Henry Orient, The (1964)')
(5.0, "Wild Hearts Can't Be Broken (1991)")
(5.0, 'White Rose, The (Weiße Rose, Die) (1982)')
(5.0, "Where's Marlowe? (1998)")
(5.0, 'Welcome Home, Roscoe Jenkins (2008)')
(5.0, 'War and Peace (Jang Aur Aman) (2001)')
